## Final Code

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.animation as animation
from matplotlib.animation import FFMpegWriter
import math

%matplotlib qt

def generate_random_grid(width, height, num_rooms, seed=None):
    if seed is not None:
        np.random.seed(seed)
        
    grid = np.zeros((height, width), dtype=int)
    
    # Generate rooms
    rooms = []
    for room in range(num_rooms):
        room_width = np.random.randint(2, width // 3)
        room_height = np.random.randint(2, height // 3)

        x_start = np.random.randint(1, width - room_width - 1)
        y_start = np.random.randint(1, height - room_height - 1)

        grid[y_start:y_start + room_height, x_start:x_start + room_width] = 1
        rooms.append(((x_start + x_start + room_width) // 2, (y_start + y_start + room_height) // 2))

    # Connect rooms with hallways
    for i in range(len(rooms) - 1):
        x1, y1 = rooms[i]
        x2, y2 = rooms[i + 1]
        draw_hallway(grid, x1, y1, x2, y2)
        
    # position search team
    flag = False
    for i in range(grid.shape[0]):
        for j in range(grid.shape[1]):
            if grid[i, j] == 1:
                grid[i, j] = 9
                position = [i, j]
                print(position)
                flag = True
                break
        if flag:
            break
            
    # position hostage
    flag = False
    for i in np.arange(grid.shape[0]-1, -1, -1):
        for j in np.arange(grid.shape[1]-1, -1, -1):
            if grid[i, j] == 1:
                grid[i, j] = 5
                position = [i, j]
                print(position)
                flag = True
                break
        if flag:
            break

    return grid

def draw_hallway(grid, x1, y1, x2, y2):
    while x1 != x2 or y1 != y2:
        if x1 < x2:
            x1 += 1
        elif x1 > x2:
            x1 -= 1
        if y1 < y2:
            y1 += 1
        elif y1 > y2:
            y1 -= 1
        grid[y1, x1] = 1

def random_walk_2d_on_grid(grid, n):
    height, width = grid.shape
    curr_x = 3.5
    curr_y = 16.5
    x = np.array([3.5])
    x = np.append(x, np.zeros(n-1))
    y = np.array([16.5])
    y = np.append(y, np.zeros(n-1))
    move_probabilities = [0.50, 0.50, 0.50, 0.50]
    
    def update(step, x, y, scatter):
        nonlocal curr_x, curr_y
        x_step = np.random.choice([-1, 1], p=move_probabilities[2:])
        y_step = np.random.choice([-1, 1], p=move_probabilities[:2])

        # Update coordinates, ensuring not to go outside the grid boundaries
        x[step] = max(0, min(width - 1, x[step - 1] + x_step))
        y[step] = max(0, min(height - 1, y[step - 1] + y_step))

        # If the new position has a wall, stay in the same position
        grid_posx = int(x[step])
        grid_posy = height - math.ceil(y[step])

        if grid[grid_posy, grid_posx] == 0:
            x[step] = x[step - 1]
            y[step] = y[step - 1]

        curr_x = x[step]
        curr_y = y[step]
        print(curr_x, curr_y)
        scatter.set_offsets(np.c_[curr_x, curr_y])
        print(step)
        if curr_x == 23.5 and curr_y == 4.5:
            ani.event_source.stop()
            print("Reached the destination!")
            show_custom_image()
            return x, y
        
    def show_custom_image():
        # Clear the existing plot
        plt.clf()

        # Display the custom image
        plt.imshow(custom_image, extent=[0, width, 0, height], alpha=0.5)
        plt.title('Search and Rescue Random Walk')
        plt.axis('off')
        plt.show()

    fig, ax = plt.subplots(figsize=(10, 10))
    scatter = ax.scatter(curr_x, curr_y, marker='o', color='red', label='Search Team')
    ax.plot(23.5, 4.5, marker='o', color='blue', label='Hostage')
    ax.imshow(grid, cmap='gray', origin='upper', extent=[0, width, 0, height])
    plt.title('Search and Rescue Random Walk')
    plt.xlabel('X-coordinate')
    plt.ylabel('Y-coordinate')
    plt.legend()

    ani = animation.FuncAnimation(fig, update, frames=range(1, n), fargs=(x, y, scatter), interval=50, blit=False)

    # Save the animation as an MP4 file using FFMpegWriter
    writer = FFMpegWriter(fps=30, metadata=dict(artist='Me'), bitrate=1800)
    ani.save('random_walk_animation.mp4', writer=writer)

    plt.show()

# Usage
seed = 106
width = 30
height = 20
num_rooms = 5

# Load image
custom_image = plt.imread('hostage_found.jpeg')

random_grid = generate_random_grid(width, height, num_rooms, seed)
random_walk_2d_on_grid(random_grid, 6000)